In [1]:
import pandas as pd
import pandas as pd
import numpy as np
import folium
import json
import requests
import os
from shapely.geometry import Point, Polygon

In [2]:
# geojson files exported from .shp with QGIS (EPSG:4326 WGS 84)
warsaw_geofile = 'geodata/Warsaw_districts/warsaw_districts.geojson'
cracow_geofile = 'geodata/Cracow_districts/cracow_districts.geojson'

In [3]:
with open(warsaw_geofile) as w:
    warsaw_geojson = json.load(w)

In [4]:
with open(cracow_geofile) as c:
    cracow_geojson = json.load(c)

In [5]:
districts_names = []
for x in warsaw_geojson['features']:
    districts_names.append(x['properties']['nazwa_dzie'])

In [7]:
test_density = list(range(len(districts_names)))

In [8]:
df = pd.DataFrame([districts_names, test_density]).T
df.columns = ['nazwa_dzie', 'Density']

In [59]:
warsaw_coordinates = [52.2297700, 21.0117800]
warsaw_map = folium.Map(location=warsaw_coordinates, zoom_start=11)
warsaw_map.choropleth(
    geo_data=warsaw_geojson,
    name='choropleth',
    data=df,
    columns=['nazwa_dzie', 'Density'],
    key_on='feature.properties.nazwa_dzie',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.9,
    legend_name='Density'
)
#warsaw_map

In [10]:
# cracow_coordinates = [50.06143, 19.93658]
# cracow_map = folium.Map(location=cracow_coordinates, zoom_start=11)

# folium.GeoJson(
#     cracow_geojson,
#     name='geojson'
# ).add_to(cracow_map)
# cracow_map

In [57]:
CLIENT_ID = os.environ.get('FOURSQUAREID')
CLIENT_SECRET = os.environ.get('FOURSQUARESECRET')
VERSION = '20200605'
LIMIT = 100
RADIUS=5000
OFFSET=LIMIT

In [68]:
def get_district_centers(city_geojson):
    district_centers = {}
    for district in city_geojson['features']:
        district_geometry = pd.DataFrame(
            district['geometry']['coordinates'][0][0],
            columns=['longitude', 'latitude']
        )
        district_center = [[district_geometry['latitude'].mean(), district_geometry['longitude'].mean()]]
        district_centers[district['properties']['nazwa_dzie']]=district_center
    
    district_centers = pd.DataFrame.from_dict(district_centers,
                                              orient='index',
                                              columns=['District_center'])
    
    return district_centers

In [13]:
def get_venues(district_center):
    lat, lng = district_center
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            RADIUS, 
            LIMIT)
    result = requests.get(url).json()
    
    venues = result['response']['groups'][0]['items']
    
    total_results = result['response']['totalResults']
    print('Total results: ', total_results)
    
    requests_to_perform = total_results//100
    
    for _ in range(requests_to_perform):
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&offset={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            RADIUS, 
            LIMIT,
            OFFSET
        )
        result = requests.get(url).json()
        venues.extend(result['response']['groups'][0]['items'])
        
    return venues

In [69]:
warsaw_district_centers = get_district_centers(warsaw_geojson)

In [58]:
warsaw_districts_venues = {}
for district in warsaw_district_centers.index:
    warsaw_districts_venues[district] = get_venues(warsaw_district_centers.loc[district, 'District_center'])

Total results:  239
Total results:  140
Total results:  230
Total results:  232
Total results:  153
Total results:  42
Total results:  56
Total results:  201
Total results:  142
Total results:  228
Total results:  236
Total results:  68
Total results:  137
Total results:  44
Total results:  233
Total results:  121
Total results:  73
Total results:  146


In [44]:
def check_if_inside_district(venue_coords, district_shape):
    p = Point(venue_coords)
    poly = Polygon(district_shape)
    return p.within(poly)

In [45]:
warsaw_district_centers.head()

District_center
Żoliborz         [52.2688536216614, 20.985135391429377]
Praga-Południe    [52.235168690871, 21.071138918572952]
Mokotów         [52.18866196405862, 21.052814696946914]
Wola             [52.22969762335711, 20.94634273758449]
Wilanów         [52.15030830502675, 21.091139416474352]

In [46]:
for center in warsaw_district_centers.index:
    folium.Marker(warsaw_district_centers.loc[center, 'District_center']).add_to(warsaw_map)
    #print(center)

In [61]:
for key in warsaw_districts_venues.keys():    
    for item in warsaw_districts_venues[key]:
        #print(item['venue']['name'], ' ', item['venue']['categories'][0]['name'])
        folium.Marker([item['venue']['location']['lat'], item['venue']['location']['lng']]).add_to(warsaw_map)

In [62]:
warsaw_map

In [73]:
warsaw_districts_venues['Żoliborz'][0]

{'reasons': {'count': 0,
  'items': [{'summary': 'This spot is popular',
    'type': 'general',
    'reasonName': 'globalInteractionReason'}]},
 'venue': {'id': '4baf7aa5f964a52031033ce3',
  'name': 'Park Żeromskiego',
  'location': {'address': 'Mickiewicza',
   'lat': 52.26837710113502,
   'lng': 20.988746715108583,
   'labeledLatLngs': [{'label': 'display',
     'lat': 52.26837710113502,
     'lng': 20.988746715108583}],
   'distance': 251,
   'cc': 'PL',
   'city': 'Warszawa',
   'state': 'Województwo mazowieckie',
   'country': 'Polska',
   'formattedAddress': ['Mickiewicza', 'Warszawa', 'Polska']},
  'categories': [{'id': '4bf58dd8d48988d163941735',
    'name': 'Park',
    'pluralName': 'Parks',
    'shortName': 'Park',
    'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/park_',
     'suffix': '.png'},
    'primary': True}],
  'photos': {'count': 0, 'groups': []}},
 'referralId': 'e-0-4baf7aa5f964a52031033ce3-0'}

In [74]:
def get_districts_venues(city_districts_venues):
    all_city_venues= pd.DataFrame()
    for district in city_districts_venues.keys():
        print(district)
        district_venues=[]
        for item in city_districts_venues[district]:
            x={}
            x['District']=district
            x['Name']=item['venue']['name']
            x['Category']=item['venue']['categories'][0]['name']
            x['Lat'] = item['venue']['location']['lat']
            x['Lon'] = item['venue']['location']['lng']
            x['VenueId'] = item['venue']['id']
            district_venues.append(x)
        district_df = pd.DataFrame(district_venues)
        all_city_venues = all_city_venues.append(district_df)
    return all_city_venues

In [75]:
h = get_districts_venues(warsaw_districts_venues)

Żoliborz
Praga-Południe
Mokotów
Wola
Wilanów
Wesoła
Wawer
Włochy
Ursynów
Śródmieście
Praga-Północ
Ursus
Targówek
Rembertów
Ochota
Bielany
Białołęka
Bemowo


In [76]:
h

District                            Name               Category  \
0    Żoliborz                Park Żeromskiego                   Park   
1    Żoliborz                Galeria Wypieków                 Bakery   
2    Żoliborz                    Plac Wilsona                  Plaza   
3    Żoliborz             Prochownia Żoliborz                   Café   
4    Żoliborz  Plac zabaw w Parku Żeromskiego             Playground   
..        ...                             ...                    ...   
141    Bemowo                    husarska yoo                  Trail   
142    Bemowo               Carrefour Express          Grocery Store   
143    Bemowo                 Bar Miss Sajgon  Vietnamese Restaurant   
144    Bemowo          Hotel Stawisko Klaudyn                  Hotel   
145    Bemowo                     Orient Cook       Asian Restaurant   

           Lat        Lon                   VenueId  
0    52.268377  20.988747  4baf7aa5f964a52031033ce3  
1    52.268523  20.986111  55508b67498e2dcf9038f190  
2    52.268914  20.985587  4bb771276edc76b0a92e321c  
3    52.268676  20.989228  50b68fd0e4b0132956a40f65  
4    52.267248  20.988827  4db2f35a4b226b343d6d0581  
..         ...        ...                       ...  
141  52.200740  20.920875  50962488e4b076702d276139  
142  52.198947  20.908864  4f4cfde76b7428f5d989fd1c  
143  52.198636  20.913068  5087db74e4b02c9e3d8be924  
144  52.277663  20.864516  4e70da0eb0fba1302a5fabe7  
145  52.200215  20.932604  515d7a27e4b0b437d403c23a  

[3222 rows x 6 columns]

In [77]:
len(h.VenueId.unique())

1183

In [80]:
h.shape

(1183, 6)

In [79]:
h.drop_duplicates(subset='VenueId',inplace=True)

In [88]:
def create_districts_polygons(geojson):
    polygons = {}
    for district in geojson['features']:
        polygons[district['properties']['nazwa_dzie']]=district['geometry']['coordinates'][0][0]
    return polygons

In [89]:
create_districts_polygons(warsaw_geojson)

{'Żoliborz': [[20.957550244360345, 52.266927972075955],
  [20.957595033280743, 52.26712068328835],
  [20.957577637116344, 52.26723607840504],
  [20.957537312295642, 52.26727740707875],
  [20.957761257322645, 52.267475395339645],
  [20.957815144778245, 52.267498512850246],
  [20.95787439818555, 52.26757897342375],
  [20.95791009640075, 52.26762769918745],
  [20.957907153084747, 52.26764189861664],
  [20.95793322389554, 52.26764721061744],
  [20.957923228478144, 52.26768297788135],
  [20.957920876497745, 52.26769151530553],
  [20.95793214246805, 52.26770634893295],
  [20.958270099249148, 52.26802283392484],
  [20.958467694144947, 52.26820795917454],
  [20.95868797775235, 52.26841439274213],
  [20.958872967069347, 52.268452385171436],
  [20.95894444363255, 52.26846705990273],
  [20.95915945950805, 52.268511173916025],
  [20.961263616641954, 52.27015734038829],
  [20.96171409893366, 52.27050980280468],
  [20.96176841477846, 52.27055251169258],
  [20.961853359918262, 52.27058354652189],
  [

In [81]:
warsaw_geojson

{'type': 'FeatureCollection',
 'name': 'warsaw_districts',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'nazwa_dzie': 'Żoliborz',
    'style': {'weight': 1,
     'opacity': 0.9,
     'color': 'black',
     'fillOpacity': 0.7,
     'fillColor': '#d9f0a3'},
    'highlight': {}},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[20.957550244360345, 52.266927972075955],
       [20.957595033280743, 52.26712068328835],
       [20.957577637116344, 52.26723607840504],
       [20.957537312295642, 52.26727740707875],
       [20.957761257322645, 52.267475395339645],
       [20.957815144778245, 52.267498512850246],
       [20.95787439818555, 52.26757897342375],
       [20.95791009640075, 52.26762769918745],
       [20.957907153084747, 52.26764189861664],
       [20.95793322389554, 52.26764721061744],
       [20.957923228478144, 52.26768297788135],
       [20.957920876497745, 52.26769151530553],

In [ ]:
h['correct_district'] = 

In [3]:
%history -g

 2/1:
def read_landsat_images (folder_name):
    file_list = os.listdir(folder_name)
    chanel_list = []
    for f in fiel_list:
        if (f.startswith('LC') and f.endswith('.tif')):
            if  'band' in f:
                chanel_list.append(folder_name +f)
    channel_list.sort()
    channel_numbers = np.arrange(1,8)
    bands_dictionary = dict(zip(channel_numbers, channel_list))
    return bands_directory

#test
satelite_images = read_landsat_images('LC081900232018080301T1-SC20181218151707')
for band in satelite_images:
    print(band, satelite_images[band])
 2/2:
import os
import numpy as np
import rasterio as rio
import rasterio.mask as rmask
import fiona as fio
import matplotlib as plt
 2/3:
# Kod wpisujemy normalnie w komórkach. Shift + Enter realizuje kod w danej komórce.
# Komenda poniżej obowiązkowa w celu poprawnego wyświetlania obrazów.
%matplotlib notebook
 2/4:
def read_landsat_images (folder_name):
    file_list = os.listdir(folder_name)
    chanel_list = []
    f

22/8: ufo_df['Date_occured_len']=ufo_df['Date_occured'].astype(str).str.len()
22/9: ufo_df['Date_reported_len']=ufo_df['Date_reported'].astype(str).str.len()
22/10: ufo_df.head()
22/11: bad_date_df = ufo_df.loc[(ufo_df['Date_occured_len'] != 8) | (ufo_df['Date_reported_len'] != 8)]
22/12: bad_date_df.sort_values(by=['Date_occured_len'])
22/13: bad_date_df.info()
22/14: ufo_df[ufo_df['Date_occured_len'] != 8].count()['Date_occured_len']
22/15: ufo_df[ufo_df['Date_reported_len'] != 8].count()['Date_reported_len']
22/16: ufo_df.drop(ufo_df[ufo_df.Date_occured_len !=8].index, inplace=True)
22/17: pd.to_datetime(ufo_df.loc[0]['Date_occured'],format='%Y%m%d')
22/18: ufo_df['zerodate'] = ufo_df['Date_occured'].astype(str).str.match(r'....00')
22/19: ufo_df.loc[ufo_df['zerodate'] == True]
22/20: ufo_df.drop(ufo_df.loc[ufo_df['zerodate'] == True].index, inplace=True)
22/21: ufo_df.sort_values(by=['Date_occured']).head()
22/22: ufo_df.drop(40901, inplace=True)
22/23: ufo_df['Date_occured']=pd.to

26/28: pd.__dict__['DataFrame']
26/29: pd.__dict__['DataFrame'].__dict__
26/30: dir(pd.DataFrame)
26/31: hwg_df.quantile(q=[x*0.2 for x in range(0,11)])
26/32: import pandas as pd
26/33: heights_weights_gender_data = '/users/wioletanytko/documents/workspace/r/umapro/02-Exploration/data/01_heights_weights_genders.csv'
26/34:
hwg_df = pd.read_csv(
    heights_weights_gender_data)
26/35: hwg_df.head()
26/36: hwg_df.Height =hwg_df.Height * 2.54
26/37: hwg_df.Weight = hwg_df.Weight * 0.454
26/38: hwg_df.describe()
26/39: hwg_df.quantile(q=[x*0.2 for x in range(0,11)])
26/40: 'DataFrame' in pd.__dict__
26/41: hwg_df.describe()
26/42: hwg_df.quantile(q=[x*0.2 for x in range(0,11)])
26/43: hwg_df.quantile(q=[x*0.2 for x in range(0,6)])
26/44: hwg_df.quantile(q=0.25), hwg_df.quantile(q=0.75)
26/45: hwg_df.Height.quantile(q=0.25), hwg_df.Height.quantile(q=0.75)
26/46: hwg_df.Height.quantile(q=0.05), hwg_df.Height.quantile(q=0.95)
26/47: help(avg)
26/48:
def my_var(x):
    m = sum(x)/len(x)
    r

34/93: sorted(all_spam, key=str.len())
34/94: sorted(all_spam, key=len(str))
34/95: sorted(all_spam, key=lambda x: len(x))
34/96: sorted(test_corpus, key=lambda x: len(x))
34/97: sorted(test_corpus, key=lambda x: len(x), reverse=True)
34/98: [x in test_corpus if len(x)>20]
34/99: [x for x in test_corpus if len(x)>20]
34/100: len([x for x in test_corpus if len(x)>20])
34/101: len(test_corpus)
34/102:
def build_corpus(messages_vector):
    corpus = set()
    for message in messages_vector:
        message_words = [x for x in re.findall(r'\w+', message) if len(x)<20 and not any(i.isdigit() for i in x)] 
        #print(message_words)
        corpus = corpus | set(message_words)
    return list(corpus)
34/103: test_corpus = build_corpus(all_spam)
34/104: print(test_corpus)
34/105: len(test_corpus)
34/106:
for i, message in enumerate(all_spam):
    occurances = count_words(message, test_corpus)
    for key in occurances.keys():
        matrix.at[key,i] = occurances[key]
34/107: matrix.head(5

41/47: classify_email([all_spam[7]])
41/48:
def classify_email(email, prior=0.5, c=0.2):
    matrix = create_matrix(email)
    #print(matrix.head(10))
    common_words = set(matrix_spam.index).intersection(set(matrix.index))
    print(common_words)
    number_of_words = len(re.findall(r'\w+', email[0]))
    number_of_common_words = len(common_words)
    print()
    number_of_uncommon_words = number_of_words - number_of_common_words
    if number_of_common_words < 1:
        return prior*c**number_of_words
    else:
        probability_common = np.prod([matrix_spam.at[word,'documents_percentage'] for word in common_words])
        print('probability_common: ', probability_common)
        probability_uncommon = c**number_of_uncommon_words
        print('probability_uncommon: ', probability_uncommon)
        return(prior*probability_common*probability_uncommon)
41/49: classify_email([all_spam[7]])
41/50: classify_email([all_spam[70]])
41/51:
def classify_email(email, prior=0.5, c=0.3):
  

...

141/61: df_postal_codes = df_list[0]
141/62: df_postal_code
141/63: df_postal_codes
141/64: >This method return *list*, and correct dataframe is it's first element
141/65: df_postal_codes.head()
141/66: df_list = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')
141/67: df_postal_codes = df_list[0]
141/68: df.postal_codes.isnull().sum()
141/69: df_postal_codes.isnull().sum()
141/70: df_postal_codes.isnull().count()
141/71: df_postal_codes.isnull().sum()
141/72: df_postal_codes['Neighborhood']
141/73: df_postal_codes['Neighborhood']=='Not assigned'
141/74: dfdf_[postal_codes['Neighborhood']=='Not assigned']
141/75: df_postal_codes[df_postal_codes['Neighborhood']=='Not assigned']
141/76: df_postal_codes[df_postal_codes['Neighborhood']=='Not assigned']
141/77: df_postal_codes[df_postal_codes['Neighborhood']=='Not assigned'].count()
141/78: df_postal_codes = df_postal_codes[~(df_postal_codes['Borough']=='Not assigned')]
141/79: df_postal_codes.isnull().sum()
1

144/97:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped
144/98: toronto_onehot['Neighborhood']
144/99:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")
toronto_onehot.columns
144/100: toronto_venues.head()
144/101:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")
toronto_onehot['Neighborhood']
144/102: toronto_venues[['Venue Category']]
144/103: 'Neighborhood'.isin(toronto_venues[['Venue Category']])
144/104: toronto_venues[['Venue Category']]
144/105: toronto_venues[['Venue Category']].loc[toronto_venues[['Venue Category']]=='Neighborhood']
144/106: toronto_venues[['Venue Category']]
144/107: type(toronto_venues[['Venue Category']])
144/108: toronto_venues[['Venue Category']]=='Neighborhood'
144/109: toronto_venues[['Venue Category']].loc[toronto_venues[['Venue Category']]=='Neighborhood']
144/110: toronto_venues[

145/156:
df = pd.DataFrame([districts_names, test_density]).T
df.columns = ['nazwa_dzie', 'Density']
145/157:
warsaw_coordinates = [52.2297700, 21.0117800]
warsaw_map = folium.Map(location=warsaw_coordinates, zoom_start=11)
warsaw_map.choropleth(
    geo_data=warsaw_geojson,
    name='choropleth',
    data=df,
    columns=['nazwa_dzie', 'Density'],
    key_on='feature.properties.nazwa_dzie',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Density'
)
warsaw_map
145/158: warsaw_geofile = 'geodata/warsaw_districts/warsaw_districts.geojson'
145/159:
with open(warsaw_geofile) as w:
    warsaw_geojson = json.load(w)
145/160:
districts_names = []
for x in warsaw_geojson['features']:
    districts_names.append(x['properties']['nazwa_dzie'])
145/161: test_density = list(range(len(districts_names)))
145/162:
df = pd.DataFrame([districts_names, test_density]).T
df.columns = ['nazwa_dzie', 'Density']
145/163:
warsaw_coordinates = [52.2297700, 21.0117800]
warsaw_

148/7:
districts_names = []
for x in warsaw_geojson['features']:
    districts_names.append(x['properties']['nazwa_dzie'])
148/8: test_density = list(range(len(districts_names)))
148/9:
df = pd.DataFrame([districts_names, test_density]).T
df.columns = ['nazwa_dzie', 'Density']
148/10:
warsaw_coordinates = [52.2297700, 21.0117800]
warsaw_map = folium.Map(location=warsaw_coordinates, zoom_start=11)
warsaw_map.choropleth(
    geo_data=warsaw_geojson,
    name='choropleth',
    data=df,
    columns=['nazwa_dzie', 'Density'],
    key_on='feature.properties.nazwa_dzie',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.9,
    legend_name='Density'
)
#warsaw_map
148/11:
cracow_coordinates = [50.06143, 19.93658]
cracow_map = folium.Map(location=cracow_coordinates, zoom_start=11)

folium.GeoJson(
    cracow_geojson,
    name='geojson'
).add_to(cracow_map)
cracow_map
148/12:
CLIENT_ID = os.environ.get('FOURSQUAREID')
CLIENT_SECRET = os.environ.get('FOURSQUARESECRET')
VERSION = '202

warsaw_districts_venues = {}
for district in warsaw_district_centers.index:
    print(district)
    warsaw_districts_venues[district] = get_venues(warsaw_district_centers.loc[district, 'District_center'])
150/106:
def get_district_centers(city_geojson):
    district_centers = {}
    for district in city_geojson['features']:
        district_geometry = pd.DataFrame(
            district['geometry']['coordinates'][0][0],
            columns=['longitude', 'latitude']
        )
        district_center = [[district_geometry['latitude'].mean(), district_geometry['longitude'].mean()]]
        district_centers[district['properties']['nazwa_dzie']]=district_center
    
    district_centers = pd.DataFrame.from_dict(district_centers,
                                              orient='index',
                                              columns=['District_center'])
    
    return district_centers
150/107:
def get_districts_venues(city_districts_venues):
    all_city_venues= pd.DataFrame()
   

In [ ]:
def pin_venues(venues_df,city_map):
    for i in venues_df.index:
        folium.Marker([venues_df.loc[i,'Lat'], venues_df.loc[i,'Lon']]).add_to(city_map)

In [ ]:
def calculate_radius(district_name):
    center_coords = warsaw_district_centers.loc[district_name, 'District_center']
    center_point = Point(center_coords[1], center_coords[0])
    
    polygon_points = []
    for point_coords in warsaw_districts_polygons [district_name]:
        polygon_point = Point(point_coords[0], point_coords[1])
        polygon_points.append(polygon_point)
    
    distances = []
    for point in polygon_points:
        distance_to_center = center_point.distance(point)
        distances.append(distance_to_center)
        
    max_distance = max(distances)
    factor = 0.6157*111.3*1000
    max_distance_meters = int(max_distance*factor)
    
    return max_distance_meters

In [ ]:
warsaw_districts_radiuses = {}
for district in warsaw_district_centers.index:
    warsaw_districts_radiuses[district] = calculate_radius(district)

In [ ]:
def get_venues(district_center, radius):
    RADIUS = radius
    lat, lng = district_center
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            RADIUS, 
            LIMIT)
    result = requests.get(url).json()
    
    venues = result['response']['groups'][0]['items']
    
    total_results = result['response']['totalResults']
    print('\tTotal results: ', total_results, '\n')
    
    #checking if there is more results -if true, next request with offset is send
    requests_to_perform = total_results//100
    
    for _ in range(requests_to_perform):
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&offset={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            RADIUS, 
            LIMIT,
            OFFSET
        )
        result = requests.get(url).json()
        venues.extend(result['response']['groups'][0]['items'])
        
    return venues

In [ ]:
warsaw_districts_venues_foursquare = {}
for district in warsaw_district_centers.index:
    print(district)
    warsaw_districts_venues_foursquare[district] = get_venues(
        warsaw_district_centers.loc[district, 'District_center'],
        warsaw_districts_radiuses[district])

In [ ]:
def create_districts_polygons(geojson):
    polygons = {}
    for district in geojson['features']:
        polygons[district['properties']['nazwa_dzie']]=district['geometry']['coordinates'][0][0]
    return polygons

In [ ]:
warsaw_districts_polygons = create_districts_polygons(warsaw_geojson)

In [ ]:
def check_if_inside_district(venue_coords, district_shape):
    p = Point(venue_coords)
    poly = Polygon(district_shape)
    return p.within(poly)

In [ ]:
warsaw_districts_venues.reset_index(inplace=True)

In [ ]:
for i in warsaw_districts_venues.index:
    warsaw_districts_venues.loc[i, 'Inside'] = check_if_inside_district(
                                        [warsaw_districts_venues.loc[i,'Lon'], warsaw_districts_venues.loc[i,'Lat']],
                                        warsaw_districts_polygons[warsaw_districts_venues.loc[i,'District']])

In [ ]:
warsaw_districts_venues = warsaw_districts_venues.loc[warsaw_districts_venues['Inside']==True]

In [ ]:
warsaw_districts_venues = get_districts_venues(warsaw_districts_venues_foursquare)

In [ ]:
warsaw_top5 = warsaw_districts_venues.groupby('Category').count().sort_values(by='VenueId', ascending=False).head()

In [ ]:
def extract_data(district,district_venues_foursquare):
    district_venues=[]
    for item in district_venues_foursquare:
        x={}
        x['District']=district
        x['Name']=item['venue']['name']
        x['Category']=item['venue']['categories'][0]['name']
        x['Lat'] = item['venue']['location']['lat']
        x['Lon'] = item['venue']['location']['lng']
        x['VenueId'] = item['venue']['id']
        district_venues.append(x)
    district_df = pd.DataFrame(district_venues)
    return district_df

In [ ]:
def get_districts_venues(city_districts_venues):
    all_city_venues= pd.DataFrame()
    for district in city_districts_venues.keys():
        district_df = extract_data(district, city_districts_venues[district])
        district_df['District'] = district
        all_city_venues = all_city_venues.append(district_df)
    return all_city_venues

In [ ]:
def check_if_inside_district(venue_coords, district_shape):
    p = Point(venue_coords)
    poly = Polygon(district_shape)
    return p.within(poly)

In [ ]:
cracow_districts_names = []
for x in cracow_geojson['features']:
    cracow_districts_names.append(x['properties']['nazwa'])

In [ ]:
cracow_test_density = list(range(len(districts_names)))
df = pd.DataFrame([cracow_districts_names, test_density]).T
df.columns = ['nazwa', 'Density']

In [ ]:
def create_cracow_map():    
    cracow_coordinates = [50.06143, 19.93658]
    cracow_map = folium.Map(location=cracow_coordinates, zoom_start=11)
    cracow_map.choropleth(
        geo_data=cracow_geojson,
        name='choropleth',
        data=df,
        columns=['nazwa', 'Density'],
        key_on='feature.properties.nazwa',
        fill_color='YlGn',
        fill_opacity=0.7,
        line_opacity=0.9,
        legend_name='Density'
    )
    return cracow_map
150/488:
cracow_map = create_cracow_map()

In [ ]:
def create_cracow_polygons(geojson):
    polygons = {}
    for district in geojson['features']:
        polygons[district['properties']['nazwa']]=district['geometry']['coordinates'][0][0]
    return polygons

In [ ]:
def get_cracow_centers(city_geojson):
    district_centers = {}
    for district in city_geojson['features']:
        district_geometry = pd.DataFrame(
            district['geometry']['coordinates'][0][0],
            columns=['longitude', 'latitude']
        )
        district_center = [[district_geometry['latitude'].mean(), district_geometry['longitude'].mean()]]
        district_centers[district['properties']['nazwa']]=district_center
    
    district_centers = pd.DataFrame.from_dict(district_centers,
                                              orient='index',
                                              columns=['District_center'])
    
    return district_centers
cracow_districts_centers = get_cracow_centers(cracow_geojson)

In [ ]:
cracow_districts_polygons = create_cracow_polygons(cracow_geojson)

In [ ]:
def calculate_cracow_radius(district_name):
    center_coords = cracow_districts_centers.loc[district_name, 'District_center']
    center_point = Point(center_coords[1], center_coords[0])
    
    polygon_points = []
    for point_coords in cracow_districts_polygons [district_name]:
        polygon_point = Point(point_coords[0], point_coords[1])
        polygon_points.append(polygon_point)
    
    distances = []
    for point in polygon_points:
        distance_to_center = center_point.distance(point)
        distances.append(distance_to_center)
        
    max_distance = max(distances)
    factor = 0.6157*111.3*1000
    max_distance_meters = int(max_distance*factor)
    
    return max_distance_meters

In [ ]:
cracow_districts_radiuses = {}
for district in cracow_districts_centers.index:
    cracow_districts_radiuses[district] = calculate_cracow_radius(district)

In [ ]:
cracow_districts_venues_foursquare = {}
for district in cracow_districts_centers.index:
    print(district)
    cracow_districts_venues_foursquare[district] = get_venues(
        cracow_districts_centers.loc[district, 'District_center'],
        cracow_districts_radiuses[district])

In [ ]:
cracow_districts_venues = get_districts_venues(cracow_districts_venues_foursquare)
cracow_districts_venues.reset_index(inplace=True)

In [ ]:
for i in cracow_districts_venues.index:
    cracow_districts_venues.loc[i, 'Inside'] = check_if_inside_district(
                                        [cracow_districts_venues.iloc[i]['Lon'], cracow_districts_venues.loc[i]['Lat']],
                                        cracow_districts_polygons[cracow_districts_venues.iloc[i]['District']])

In [ ]:
cracow_districts_venues = cracow_districts_venues.loc[cracow_districts_venues['Inside']==True]
cracow_top5 = cracow_districts_venues.groupby('Category').count().sort_values(by='VenueId', ascending=False).head()

In [ ]:
cracow_map = create_cracow_map()
for i in cracow_districts_venues.index:    
    folium.Marker([cracow_districts_venues.loc[i,'Lat'], cracow_districts_venues.loc[i,'Lon']]).add_to(cracow_map)

In [ ]:
top_categories = warsaw_top5.add(cracow_top5, fill_value=0)

In [ ]:
top_5_categories = top_categories.head().index
top_5_categories

In [ ]:
warsaw_districts_wiki = 'https://pl.wikipedia.org/wiki/Podział_administracyjny_Warszawy'
cracow_districts_wiki = 'https://pl.wikipedia.org/wiki/Podział_administracyjny_Krakowa'

In [ ]:
warsaw_districts_df = pd.read_html(warsaw_districts_wiki)